Proof of <a class="ProveItLink" href="../../../../../../_theory_nbs_/theory.ipynb">proveit</a>.<a class="ProveItLink" href="../../../../../_theory_nbs_/theory.ipynb">physics</a>.<a class="ProveItLink" href="../../../../_theory_nbs_/theory.ipynb">quantum</a>.<a class="ProveItLink" href="../../theory.ipynb">QPE</a>.<a class="ProveItLink" href="../../theorems.ipynb#_psi_t_formula">_psi_t_formula</a> theorem
========

In [1]:
import proveit
theory = proveit.Theory() # the theorem's theory
from proveit import a, b, c, k, m, n, t, P, defaults, Function
from proveit.linear_algebra import ScalarMult, TensorProd, VecSpaces
from proveit.logic import Equals, InSet
from proveit.numbers import (
        zero, one, two, i, e, pi, Add, Sum, Exp, Less, LessEq, Mult, frac, Neg, subtract)
from proveit.numbers import Complex, Interval, Natural
from proveit.numbers.number_sets.natural_numbers import fold_forall_natural_pos
from proveit.physics.quantum import Ket, NumKet
from proveit.physics.quantum.QPE import _phase, _phase_is_real, _psi_t_def

In [2]:
%proving _psi_t_formula

Keep the $2$ in $2 \pi i$ from combining with powers of $2$:

In [3]:
Exp.change_simplification_directives(factor_numeric_rational=True)

In [4]:
# the induction theorem for positive naturals
fold_forall_natural_pos

|- forall_{P} ((P(1) and [forall_{m in NaturalPos | P(m)} P(m + 1)]) => [forall_{n in NaturalPos} P(n)])

In [5]:
# instantiate the induction theorem
induction_inst = fold_forall_natural_pos.instantiate(
    {Function(P,t):_psi_t_formula.instance_expr, m:t, n:t})

### Base Case

In [6]:
VecSpaces.default_field=Complex
defaults.assumptions = _psi_t_formula.all_conditions()

In [7]:
base_case = induction_inst.antecedent.operands[0]

We have $|\psi_{t}\rangle$ defined as a tensor product (the result of the first phase of the quantum circuit, and the LHS of Nielsen & Chuang's identity 5.20 on pg 222):

In [8]:
_psi_t_def

|- forall_{t in NaturalPos} (|psi_{t}> = (((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t - 1} * phase} * |1〉))) otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t - 2} * phase} * |1〉))) otimes  ... otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{0} * phase} * |1〉)))))

In [9]:
_psi_t_as_tensor_prod = _psi_t_def.instantiate()

For $\psi'_{1}$, we prove a useful equality then instantiate the `psi_t_def` with $t=1$:

In [10]:
psi_1_def = _psi_t_def.instantiate({t:one})

Then show that the summation formula also gives the same qbit result

In [11]:
sum_0_to_1 = base_case.rhs

In [12]:
sum_0_to_1_processed_01 = sum_0_to_1.inner_expr().operands[1].partitioning_first()

In [13]:
# finish off the Base Case
base_case_jdgmt = sum_0_to_1_processed_01.sub_left_side_into(psi_1_def)

### Inductive Step

In [14]:
inductive_step = induction_inst.antecedent.operands[1]

In [15]:
defaults.assumptions = defaults.assumptions + inductive_step.conditions.entries

First, partition the summation:
$\sum_{k=0}^{2^{t+1}-1} e^{2\pi i \varphi k} |k\rangle_{t+1} = \sum_{k=0}^{2^{t}-1} e^{2\pi i \varphi k} |k\rangle_{t+1} + \sum_{k=2^{t}}^{2^{t+1}-1} e^{2\pi i \varphi k} |k\rangle_{t+1}$

In [16]:
desired_domain = _psi_t_formula.instance_expr.rhs.scaled.domain

In [17]:
summation_partition_01 = (
    inductive_step.instance_expr.rhs.operands[1]
    .partitioning(desired_domain.upper_bound))

Then shift the second summation of that partition, so that the two summations then have the same index domain:

In [18]:
summation_partition_02 = (summation_partition_01.inner_expr().rhs.
                          operands[1].shift(Neg(Exp(two, t))))

We want to rewrite the summand of that 2nd summation on the rhs now by (1) expanding the exponential term and (2) rewriting the $|k+2^t{\rangle}_{t+1}$ ket as $|1\rangle \otimes |k{\rangle}_t$. This takes a little work.

In [19]:
rhs_2nd_sum = summation_partition_02.rhs.operands[1]

In [20]:
summand_processed_01 = rhs_2nd_sum.summand.inner_expr().operands[0].exponent.distribution(
    4, assumptions=[*defaults.assumptions,
                    rhs_2nd_sum.condition])

In [21]:
summand_processed_02 = (
    summand_processed_01.inner_expr().rhs.operands[0]
    .exponent_separate(
        assumptions=[*defaults.assumptions,
                     InSet(k, Interval(zero, subtract(Exp(two, t), one)))]))

In [22]:
# Avoid recombining these via auto-simplification
defaults.preserved_exprs = set([summand_processed_02.rhs.scalar])

In [23]:
from proveit.physics.quantum.algebra import prepend_num_ket_with_one_ket
prepend_num_ket_with_one_ket

|- forall_{n in NaturalPos} [forall_{k in {0 .. 2^{n} - 1}} (|2^{n} + k〉_{n + 1} = (|1〉 otimes |k〉_{n}))]

In [24]:
prepend_num_ket_with_one_ket_inst = prepend_num_ket_with_one_ket.instantiate(
        {n: t, k: k},
        assumptions=[*defaults.assumptions, InSet(k, Interval(zero, subtract(Exp(two, t), one)))])

In [25]:
summand_processed_03 = (
    summand_processed_02.inner_expr().rhs.operands[1]
    .substitute(prepend_num_ket_with_one_ket_inst))

In [26]:
# reminder of summation_partition_03
summation_partition_02

{t in NaturalPos} |- (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1})) = ((Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1})) + (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * (k + 2^{t})} * |k + 2^{t}〉_{t + 1})))

In [27]:
summation_partition_04 = (
    summation_partition_02.inner_expr().rhs.operands[1].summand.substitute(
        summand_processed_03))

Also process the summand in the 1st sum on the rhs, converting the ket $|k\rangle_{t+1}$ to the tensor product $|0\rangle \otimes |k\rangle_{t}$:

In [28]:
# pull up the relevant NumKet theorem
from proveit.physics.quantum.algebra import prepend_num_ket_with_zero_ket
prepend_num_ket_with_zero_ket

|- forall_{n in NaturalPos} [forall_{k in {0 .. 2^{n} - 1}} (|k〉_{n + 1} = (|0〉 otimes |k〉_{n}))]

In [29]:
# instantiate the theorem for our specific case
prepend_num_ket_with_zero_ket_inst = prepend_num_ket_with_zero_ket.instantiate(
        {n: t, k: k},
        assumptions=[*defaults.assumptions, InSet(k, Interval(zero, subtract(Exp(two, t), one)))])

In [30]:
# use our instantiation to substitute
summation_partition_05 = (
    summation_partition_04.inner_expr().rhs.operands[0].summand.scaled.substitute(
    prepend_num_ket_with_zero_ket_inst))

In [31]:
coef = inductive_step.instance_expr.rhs.scalar
summation_partition_06 = summation_partition_05.scalar_mult_both_sides(coef)

In [32]:
# Recall our inductive hypothesis:
inductive_hypothesis = defaults.assumptions[-1]

In [33]:
conclusion_01 = summation_partition_06.inner_expr().rhs.factor(
        inductive_hypothesis.rhs, pull='right', field=Complex)

In [34]:
# use the inductive hypothesis:
conclusion_02 = inductive_hypothesis.sub_left_side_into(conclusion_01)

The RHS of conclusion_02 above should be equal to $|\psi_{t+1}\rangle$. Let's see how to get there. Ideally we could use the next three cells to show the rhs of the equality in `conclusion_02` is equal to $|\psi_{t+1}\rangle$

In [35]:
# reminder
_psi_t_def

|- forall_{t in NaturalPos} (|psi_{t}> = (((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t - 1} * phase} * |1〉))) otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t - 2} * phase} * |1〉))) otimes  ... otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{0} * phase} * |1〉)))))

In [36]:
psi_t_plus_one_as_tensor_prod = _psi_t_def.instantiate({t:Add(t, one)})

Now this `substitute()` step will also manage to pull the scalar coefficients out to the front in the process:

In [37]:
conclusion_03 = conclusion_02.inner_expr().rhs.operands[1].substitute(
        _psi_t_as_tensor_prod)

Now we partition the tensor product expression of $\psi_{t+1}$, so we can eventually show that it is equal to the rhs of conclusion_03.

In [38]:
psi_t_plus_one_as_tensor_prod.rhs

((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t} * phase} * |1〉))) otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{t - 1} * phase} * |1〉))) otimes  ... otimes  ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * 2^{0} * phase} * |1〉)))

In [39]:
# # we can partition the operands in the psi_{t+1} tensor prod expression
psi_t_plus_one_as_tensor_prod_02 = (
    psi_t_plus_one_as_tensor_prod.inner_expr().rhs.operands[0].split(t))

In [40]:
conclusion_03.inner_expr().rhs.substitute(psi_t_plus_one_as_tensor_prod_02.derive_reversed())

{t in NaturalPos, |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} |- ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))) = |psi_{t + 1}>

In [41]:
# # recall our earlier instantiation of the induction theorem:
induction_inst

|- ((|psi_{1}> = ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉)))) and [forall_{t in NaturalPos | |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} (|psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))))]) => [forall_{t in NaturalPos} (|psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t}))))]

We have proven both pieces of the antecedent (_i.e._, the base case and inductive case) of the instantiated induction theorem `induction_inst`, so we can now derive the consequent:

In [42]:
induction_inst.derive_consequent()

|- forall_{t in NaturalPos} (|psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t}))))

_psi_t_formula has been proven.  Now simply execute "%qed".


In [43]:
%qed

proveit.physics.quantum.QPE._psi_t_formula has been proven.


step type	requirements	statement
0	modus ponens	1, 2	|- forall_{t in NaturalPos} (|psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t}))))
1	instantiation	3, 4*, 5*, 6*	|- ((|psi_{1}> = ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉)))) and [forall_{t in NaturalPos | |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} (|psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))))]) => [forall_{t in NaturalPos} (|psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t}))))]
	P(t) : |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t}))), m : t, n : t
2	instantiation	7, 8, 9	|- (|psi_{1}> = ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉)))) and [forall_{t in NaturalPos | |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} (|psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))))]
	A : |psi_{1}> = ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉))), B : forall_{t in NaturalPos | |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} (|psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))))
3	conjecture		|- forall_{P} ((P(1) and [forall_{m in NaturalPos | P(m)} P(m + 1)]) => [forall_{n in NaturalPos} P(n)])
	proveit.numbers.number_sets.natural_numbers.fold_forall_natural_pos
4	instantiation	601, 10, 449	|- (2^{1} - 1) = 1
	x : 2^{1} - 1, y : 2 - 1, z : 1
5	instantiation	11, 12	{k in {0 .. 1}} |- |k〉_{1} = |k〉
	b : k
6	instantiation	601, 13, 14	{t in NaturalPos} |- 2^{t + 1} = (2 * 2^{t})
	x : 2^{t + 1}, y : 2^{1 + t}, z : 2 * 2^{t}
7	theorem		|- forall_{A, B | A, B} (A and B)
	proveit.logic.booleans.conjunction.and_if_both
8	instantiation	427, 15, 16	|- |psi_{1}> = ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉)))
	P(_a) : |psi_{1}> = _a, x : (1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉)), y : (1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * phase} * |1〉))
9	generalization	17	|- forall_{t in NaturalPos | |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} (|psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1}))))
10	instantiation	615, 630	|- (2^{1} - 1) = (2 - 1)
	f(_a) : _a - 1, x : 2^{1}, y : 2
11	conjecture		|- forall_{b in Natural} (|b〉_{1} = |b〉)
	proveit.physics.quantum.algebra.single_qubit_num_ket
12	instantiation	18, 19, 20	{k in {0 .. 1}} |- k in Natural
	a : k
13	instantiation	615, 126	{t in NaturalPos} |- 2^{t + 1} = 2^{1 + t}
	f(_a) : 2^{_a}, x : t + 1, y : 1 + t
14	instantiation	460, 21	{t in NaturalPos} |- 2^{1 + t} = (2 * 2^{t})
	x : 2 * 2^{t}, y : 2^{1 + t}
15	instantiation	102, 679, 22, 23*	|- |psi_{1}> = ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * phase} * |1〉)))
	t : 1
16	instantiation	615, 24	|- ((1 / sqrt(2)) * (Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉))) = ((1 / sqrt(2)) * (|0〉 + (e^{2 * pi * i * phase} * |1〉)))
	f(_a) : (1 / sqrt(2)) * _a, x : Sum_{k=0}^{1} (e^{2 * pi * i * phase * k} * |k〉), y : |0〉 + (e^{2 * pi * i * phase} * |1〉)
17	instantiation	460, 25	{t in NaturalPos, |psi_{t}> = ((1 / 2^{t / 2}) * (Sum_{k=0}^{2^{t} - 1} (e^{2 * pi * i * phase * k} * |k〉_{t})))} |- |psi_{t + 1}> = ((1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1})))
	x : (1 / 2^{(t + 1) / 2}) * (Sum_{k=0}^{(2 * 2^{t}) - 1} (e^{2 * pi * i * phase * k} * |k〉_{t + 1})), y : |psi_{t + 1}>
18	conjecture		|- forall_{a in Integer | a >= 0} (a in Natural)
	proveit.numbers.number_sets.integers.nonneg_int_is_natural
19	instantiation	682, 26, 28	{k in {0 .. 1}} |- k in Integer
	A : {0 .. 1}, B : Integer, x :